In [69]:
import os
import pandas as pd
import numpy as np
import sys
import copy
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [77]:
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.get_matches() # 2-1
self.initialize_state() # 2-2
self.assign_indices() # 2-3
self.p2UPLindices2inc_edge_ids

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 초기화 신호가 지정되었습니다. (우회전 : g)
2-3. 유턴 인덱스 / 비보호좌회전 인덱스를 지정했습니다.


{'i0': {},
 'i1': {},
 'i2': {},
 'i3': {},
 'i6': {8: ['-571542115_01']},
 'i7': {2: ['571542073_01']},
 'i8': {},
 'i9': {}}

In [124]:
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.get_matches() # 2-1
self.initialize_state() # 2-2
self.assign_indices() # 2-3

# match6 : 신호 배정
for i, row in self.match6.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    state_list = copy.deepcopy(self.node2init[node_id])
    self.match6.at[i, 'state'] = ''.join(state_list)
    if (pd.isna(inc_edge_id)) or (pd.isna(out_edge_id)):
        continue
    inc_edge = self.net.getEdge(inc_edge_id)
    out_edge = self.net.getEdge(out_edge_id)
    for conn in inc_edge.getConnections(out_edge):
        index = conn.getTLLinkIndex()
        if index >= 0:
            state_list[index] = 'G'
    self.match6.at[i, 'state'] = ''.join(state_list)

# mactch6 : 비보호좌회전 신호 배정
for i, row in self.match6[self.match6.node_id.isin(self.parent_ids)].iterrows():
    parent_id = row.node_id
    state = row.state
    UPLindices2inc_edge_ids = self.p2UPLindices2inc_edge_ids[parent_id]
    for UPLindex in UPLindices2inc_edge_ids:
        inc_edge_ids = UPLindices2inc_edge_ids[UPLindex]
        if inc_edge_ids:
            if inc_edge_id in inc_edge_ids:
                state = state[:UPLindex] + 'g' + state[UPLindex+1:]
                self.match6.at[i, 'state'] = state
        else: # modify_match1.py : self.match1.at[7, 'move_A'] = 17
            raise Exception(
            f"비보호좌회전 신호를 부여할 수 없습니다. \
            신호가 부여되어 있지 않은 직진 또는 좌회전 연결이 존재하는데\
            (node_id : {parent_id}, index : {UPLindex})\
            이 연결의 진입엣지(inc_edge_id : {inc_edge_id})에 부여된 신호가 없습니다.")

# mactch6 : 유턴 신호가 한번도 배정되지 않은 경우에 대해서는 유턴이동류의 신호를 항상 g로 배정
for node_id in self.u_turn_ids:
    m6 = self.match6[self.match6.node_id==node_id]
    if not len(m6):
        continue
    state_list = copy.deepcopy(self.node2init[node_id])
    state = ''.join(state_list)
    uindex = self.u2uindex[node_id]
    values_at_uindex = [state[uindex] for state in m6.state]
    uturn_assigned = ('G' in values_at_uindex)
    if not uturn_assigned:
        print('uturn not assigned')
        state = state[:uindex] + 'g' + state[uindex+1:]
        print(i, state)
        self.match6.loc[self.match6.node_id==node_id, 'state'] = state

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 초기화 신호가 지정되었습니다. (우회전 : g)
2-3. 유턴 인덱스 / 비보호좌회전 인덱스를 지정했습니다.
uturn not assigned
99 GGGGgGGGG


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
8        175         1         A        8        남        북       179   
9        175         1         B        4        북        남       001   
10       175         2         A        7        북        동       001   
11       175         2         B        3        남        서       179   
12       175         3         A        6        동        서       090   
13       175         3         B        1        동        남       090   
14       175         4         A        5        서        북       270   
15       175         4         B        2        서        동       270   

   out_angle   inc_edge_id      out_edge_id node_id turn_type      state  
8        000           NaN              NaN     u00  straight  GGGGgGGGG  
9        180           NaN              NaN     u00  straight  GGGGgGGGG  
10       090  571500487_02  571500487_01.32     u00      left  GGGGgGGGG  
11       270           NaN              NaN     u00      left  GGGGgGGGG  
12       270           NaN              NaN     u00  straight  GGGGgGGGG  
13       180           NaN              NaN     u00      left  GGGGgGGGG  
14       000           NaN              NaN     u00      left  GGGGgGGGG  
15       090           NaN              NaN     u00  straight  GGGGgGGGG

uturn not assigned
99 GGgGGG


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
26       177         1         A        8        남        북       179   
27       177         1         B        4        북        남       000   
28       177         2         A       17      NaN      NaN       NaN   
29       177         2         B       18      NaN      NaN       NaN   

   out_angle      inc_edge_id   out_edge_id node_id turn_type   state  
26       000              NaN           NaN     u20  straight  GGgGGG  
27       180              NaN           NaN     u20  straight  GGgGGG  
28       NaN  571542810_01.51  571542810_02     u20       NaN  GGgGGG  
29       NaN              NaN           NaN     u20       NaN  GGgGGG

uturn not assigned
99 GGGGgGGG


...

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
54       178         1         A        8        남        북       180   
55       178         1         B        4        북        남       000   
56       178         2         A        7        북        동       000   
57       178         2         B        3        남        서       180   
58       178         3         A        5        서        북       270   
59       178         3         B        2        서        동       270   
60       178         4         A        6        동        서       090   
61       178         4         B        1        동        남       090   

   out_angle   inc_edge_id      out_edge_id node_id turn_type     state  
54       000  571500475_02  571500475_01.26     u31  straight  GGGGgGGG  
55       180           NaN              NaN     u31  straight  GGGGgGGG  
56       090           NaN              NaN     u31      left  GGGGgGGG  
57       270           NaN              NaN     u31      left  GGGGgGGG  
58       000           NaN              NaN     u31      left  GGGGgGGG  
59       090           NaN              NaN     u31  straight  GGGGgGGG  
60       270           NaN              NaN     u31  straight  GGGGgGGG  
61       180           NaN              NaN     u31      left  GGGGgGGG

uturn not assigned
99 GGGGGGGg


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
62       178         1         A        8        남        북       180   
63       178         1         B        4        북        남       000   
64       178         2         A        7        북        동       000   
65       178         2         B        3        남        서       180   
66       178         3         A        5        서        북       270   
67       178         3         B        2        서        동       270   
68       178         4         A        6        동        서       090   
69       178         4         B        1        동        남       090   

   out_angle   inc_edge_id    out_edge_id node_id turn_type     state  
62       000           NaN            NaN     u32  straight  GGGGGGGg  
63       180  571540303_02  -571540303_02     u32  straight  GGGGGGGg  
64       090           NaN            NaN     u32      left  GGGGGGGg  
65       270           NaN            NaN     u32      left  GGGGGGGg  
66       000           NaN            NaN     u32      left  GGGGGGGg  
67       090           NaN            NaN     u32  straight  GGGGGGGg  
68       270           NaN            NaN     u32  straight  GGGGGGGg  
69       180           NaN            NaN     u32      left  GGGGGGGg

uturn not assigned
99 GGGGGGGGg


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
100       210         1         A        6        동        서       090   
101       210         1         B       18      NaN      NaN       NaN   
102       210         2         A        5        서        북       270   
103       210         2         B        2        서        동       270   
104       210         3         A        7        북        동       000   
105       210         3         B        4        북        남       000   
106       210         4         A        8        남        북       180   
107       210         4         B        3        남        서       180   

    out_angle   inc_edge_id    out_edge_id node_id turn_type      state  
100       270           NaN            NaN     u60  straight  GGGGGGGGg  
101       NaN           NaN            NaN     u60       NaN  GGGGGGGGg  
102       000  571500535_02  -571500535_02     u60      left  GGGGGGGGg  
103       090           NaN            NaN     u60  straight  GGGGGGGGg  
104       090           NaN            NaN     u60      left  GGGGGGGGg  
105       180           NaN            NaN     u60  straight  GGGGGGGGg  
106       000           NaN            NaN     u60  straight  GGGGGGGGg  
107       270           NaN            NaN     u60      left  GGGGGGGGg

In [47]:
node_id = self.u_turn_ids[0]
uindex = self.u2uindex[node_id]
m6 = self.match6[self.match6.node_id==node_id]
values_at_uindex = [state[uindex] for state in m6.state]
uturn_not_assigned = 'G' not in values_at_uindex
print(uindex)
print(uturn_not_assigned)
display(m6)
# if uturn_not_assigned:
for i, row in m6.iterrows():
    state = row.state
    state = state[:uindex] + 'g' + state[uindex+1:]
    m6.at[i, 'state'] = state
display(m6)

4
True


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
8        175         1         A        8        남        북       179   
9        175         1         B        4        북        남       001   
10       175         2         A        7        북        동       001   
11       175         2         B        3        남        서       179   
12       175         3         A        6        동        서       090   
13       175         3         B        1        동        남       090   
14       175         4         A        5        서        북       270   
15       175         4         B        2        서        동       270   

   out_angle   inc_edge_id      out_edge_id node_id turn_type      state  
8        000           NaN              NaN     u00  straight  GGGGrGGGG  
9        180           NaN              NaN     u00  straight  GGGGrGGGG  
10       090  571500487_02  571500487_01.32     u00      left  GGGGGGGGG  
11       270           NaN              NaN     u00      left  GGGGrGGGG  
12       270           NaN              NaN     u00  straight  GGGGrGGGG  
13       180           NaN              NaN     u00      left  GGGGrGGGG  
14       000           NaN              NaN     u00      left  GGGGrGGGG  
15       090           NaN              NaN     u00  straight  GGGGrGGGG

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
8        175         1         A        8        남        북       179   
9        175         1         B        4        북        남       001   
10       175         2         A        7        북        동       001   
11       175         2         B        3        남        서       179   
12       175         3         A        6        동        서       090   
13       175         3         B        1        동        남       090   
14       175         4         A        5        서        북       270   
15       175         4         B        2        서        동       270   

   out_angle   inc_edge_id      out_edge_id node_id turn_type      state  
8        000           NaN              NaN     u00  straight  GGGGgGGGG  
9        180           NaN              NaN     u00  straight  GGGGgGGGG  
10       090  571500487_02  571500487_01.32     u00      left  GGGGgGGGG  
11       270           NaN              NaN     u00      left  GGGGgGGGG  
12       270           NaN              NaN     u00  straight  GGGGgGGGG  
13       180           NaN              NaN     u00      left  GGGGgGGGG  
14       000           NaN              NaN     u00      left  GGGGgGGGG  
15       090           NaN              NaN     u00  straight  GGGGgGGGG